# Import all necessary

In [418]:
import nltk
nltk.download('punkt')

#niice

[nltk_data] Downloading package punkt to /Users/teospeece/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [419]:
import pandas
from bs4 import BeautifulSoup
import re
import nltk
import numpy
from gensim.models import word2vec

#only do next line once
#nltk.download() #in Corpora tab, download stopwords
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import CountVectorizer 
from sklearn.naive_bayes import MultinomialNB
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.svm import SVC
from sklearn.decomposition import PCA
import pandas
from sklearn.neighbors import KNeighborsClassifier


# Read in Data

In [420]:

data = pandas.read_csv("scotch_review.csv")

print(data["review.point"][0])
print(data["description"][0])
#use the Beautiful Soup package to remove html mark up
rev_soup = BeautifulSoup(data["description"][0])
print(rev_soup.get_text())

97
Magnificently powerful and intense. Caramels, dried peats, elegant cigar smoke, seeds scraped from vanilla beans, brand new pencils, peppercorn, coriander seeds, and star anise make for a deeply satisfying nosing experience. Silky caramels, bountiful fruits of ripe peach, stewed apple, orange pith, and pervasive smoke with elements of burnt tobacco. An abiding finish of smoke, dry spices, and banoffee pie sweetness. Close to perfection. Editor's Choice
Magnificently powerful and intense. Caramels, dried peats, elegant cigar smoke, seeds scraped from vanilla beans, brand new pencils, peppercorn, coriander seeds, and star anise make for a deeply satisfying nosing experience. Silky caramels, bountiful fruits of ripe peach, stewed apple, orange pith, and pervasive smoke with elements of burnt tobacco. An abiding finish of smoke, dry spices, and banoffee pie sweetness. Close to perfection. Editor's Choice


/anaconda3/lib/python3.6/site-packages/bs4/__init__.py:181: UserWarning: No parser was explicitly specified, so I'm using the best available HTML parser for this system ("lxml"). This usually isn't a problem, but if you run this code on another system, or in a different virtual environment, it may use a different parser and behave differently.

The code that caused this warning is on line 193 of the file /anaconda3/lib/python3.6/runpy.py. To get rid of this warning, change code that looks like this:

 BeautifulSoup(YOUR_MARKUP})

to this:

 BeautifulSoup(YOUR_MARKUP, "lxml")

  markup_type=markup_type))


# Clean Data

In [421]:

letters_only = re.sub("[^a-zA-Z]"," ",rev_soup.get_text())
print(letters_only)

Magnificently powerful and intense  Caramels  dried peats  elegant cigar smoke  seeds scraped from vanilla beans  brand new pencils  peppercorn  coriander seeds  and star anise make for a deeply satisfying nosing experience  Silky caramels  bountiful fruits of ripe peach  stewed apple  orange pith  and pervasive smoke with elements of burnt tobacco  An abiding finish of smoke  dry spices  and banoffee pie sweetness  Close to perfection  Editor s Choice


In [422]:
lower_case = letters_only.lower()
words = lower_case.split()
print(words)

['magnificently', 'powerful', 'and', 'intense', 'caramels', 'dried', 'peats', 'elegant', 'cigar', 'smoke', 'seeds', 'scraped', 'from', 'vanilla', 'beans', 'brand', 'new', 'pencils', 'peppercorn', 'coriander', 'seeds', 'and', 'star', 'anise', 'make', 'for', 'a', 'deeply', 'satisfying', 'nosing', 'experience', 'silky', 'caramels', 'bountiful', 'fruits', 'of', 'ripe', 'peach', 'stewed', 'apple', 'orange', 'pith', 'and', 'pervasive', 'smoke', 'with', 'elements', 'of', 'burnt', 'tobacco', 'an', 'abiding', 'finish', 'of', 'smoke', 'dry', 'spices', 'and', 'banoffee', 'pie', 'sweetness', 'close', 'to', 'perfection', 'editor', 's', 'choice']


In [423]:
def clean_sentences(raw):
    bs = BeautifulSoup(raw,'lxml')
    letters_only = re.sub("[^a-zA-Z]"," ",bs.get_text())
    lower_case = letters_only.lower()
    words = lower_case.split()
    return words

In [424]:
def review_to_sentences(review,tokenizer):
    review = review.strip()
    raw_sentences = tokenizer.tokenize(review)
    sentence_list = []
    
    for sentence in raw_sentences:
        if len(sentence) > 0:
            cl_sent = clean_sentences(sentence)
            sentence_list.append(cl_sent)
            
    return sentence_list

In [425]:
tokenizer = nltk.data.load('tokenizers/punkt/english.pickle')
data = pandas.read_csv("scotch_review.csv")
print( review_to_sentences(data['description'][0],tokenizer))

[['magnificently', 'powerful', 'and', 'intense'], ['caramels', 'dried', 'peats', 'elegant', 'cigar', 'smoke', 'seeds', 'scraped', 'from', 'vanilla', 'beans', 'brand', 'new', 'pencils', 'peppercorn', 'coriander', 'seeds', 'and', 'star', 'anise', 'make', 'for', 'a', 'deeply', 'satisfying', 'nosing', 'experience'], ['silky', 'caramels', 'bountiful', 'fruits', 'of', 'ripe', 'peach', 'stewed', 'apple', 'orange', 'pith', 'and', 'pervasive', 'smoke', 'with', 'elements', 'of', 'burnt', 'tobacco'], ['an', 'abiding', 'finish', 'of', 'smoke', 'dry', 'spices', 'and', 'banoffee', 'pie', 'sweetness'], ['close', 'to', 'perfection'], ['editor', 's', 'choice']]


In [426]:
sentences_for_all_reviews = []
for i in range(len(data)):
    sentences_for_all_reviews += \
    review_to_sentences(data['description'][i],tokenizer)

In [427]:
sentences_for_all_reviews

[['magnificently', 'powerful', 'and', 'intense'],
 ['caramels',
  'dried',
  'peats',
  'elegant',
  'cigar',
  'smoke',
  'seeds',
  'scraped',
  'from',
  'vanilla',
  'beans',
  'brand',
  'new',
  'pencils',
  'peppercorn',
  'coriander',
  'seeds',
  'and',
  'star',
  'anise',
  'make',
  'for',
  'a',
  'deeply',
  'satisfying',
  'nosing',
  'experience'],
 ['silky',
  'caramels',
  'bountiful',
  'fruits',
  'of',
  'ripe',
  'peach',
  'stewed',
  'apple',
  'orange',
  'pith',
  'and',
  'pervasive',
  'smoke',
  'with',
  'elements',
  'of',
  'burnt',
  'tobacco'],
 ['an',
  'abiding',
  'finish',
  'of',
  'smoke',
  'dry',
  'spices',
  'and',
  'banoffee',
  'pie',
  'sweetness'],
 ['close', 'to', 'perfection'],
 ['editor', 's', 'choice'],
 ['what',
  'impresses',
  'me',
  'most',
  'is',
  'how',
  'this',
  'whisky',
  'evolves',
  'it',
  's',
  'incredibly',
  'complex'],
 ['on',
  'the',
  'nose',
  'and',
  'palate',
  'this',
  'is',
  'a',
  'thick',
  'viscous

In [428]:
 #print out the nltk stop words list
print(stopwords.words("english"))

['i', 'me', 'my', 'myself', 'we', 'our', 'ours', 'ourselves', 'you', "you're", "you've", "you'll", "you'd", 'your', 'yours', 'yourself', 'yourselves', 'he', 'him', 'his', 'himself', 'she', "she's", 'her', 'hers', 'herself', 'it', "it's", 'its', 'itself', 'they', 'them', 'their', 'theirs', 'themselves', 'what', 'which', 'who', 'whom', 'this', 'that', "that'll", 'these', 'those', 'am', 'is', 'are', 'was', 'were', 'be', 'been', 'being', 'have', 'has', 'had', 'having', 'do', 'does', 'did', 'doing', 'a', 'an', 'the', 'and', 'but', 'if', 'or', 'because', 'as', 'until', 'while', 'of', 'at', 'by', 'for', 'with', 'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after', 'above', 'below', 'to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over', 'under', 'again', 'further', 'then', 'once', 'here', 'there', 'when', 'where', 'why', 'how', 'all', 'any', 'both', 'each', 'few', 'more', 'most', 'other', 'some', 'such', 'no', 'nor', 'not', 'only', 'own', 'same', 'so', 'than', '

In [429]:
num_features = 300
min_word_count = 16
num_workers = 4
context = 10
downsampling = 1e-3

model = word2vec.Word2Vec(sentences_for_all_reviews,\
    workers = num_workers, size=num_features,\
    min_count = min_word_count, window = context,\
    sample = downsampling)

model.init_sims(replace=True)

In [430]:
def make_feature_vec(words, model, num_features):
    # Pre-initialize an empty numpy array (for speed)
    feature_vec = numpy.zeros((num_features,),dtype="float32")
    nwords = 0.0
    # Loop over each word in the review and, if it is in the model's
    # vocaublary, add its feature vector to the total
    for word in words:
        if word in model.wv.vocab:
            nwords = nwords + 1.0
            feature_vec = numpy.add(feature_vec,model.wv[word])
    #fix the division by 0 when, word is not in the vocabulary
    if(nwords == 0.0):
        return feature_vec
    # Divide the result by the number of words to get the average
    feature_vec = numpy.divide(feature_vec,nwords)
    return feature_vec

In [431]:
print('original:',data['description'][0])
clean_review = clean_sentences(data['description'][0])
print('clean:',clean_review)
review_vector = make_feature_vec(clean_review, model, num_features)
print('vector:',review_vector)

original: Magnificently powerful and intense. Caramels, dried peats, elegant cigar smoke, seeds scraped from vanilla beans, brand new pencils, peppercorn, coriander seeds, and star anise make for a deeply satisfying nosing experience. Silky caramels, bountiful fruits of ripe peach, stewed apple, orange pith, and pervasive smoke with elements of burnt tobacco. An abiding finish of smoke, dry spices, and banoffee pie sweetness. Close to perfection. Editor's Choice
clean: ['magnificently', 'powerful', 'and', 'intense', 'caramels', 'dried', 'peats', 'elegant', 'cigar', 'smoke', 'seeds', 'scraped', 'from', 'vanilla', 'beans', 'brand', 'new', 'pencils', 'peppercorn', 'coriander', 'seeds', 'and', 'star', 'anise', 'make', 'for', 'a', 'deeply', 'satisfying', 'nosing', 'experience', 'silky', 'caramels', 'bountiful', 'fruits', 'of', 'ripe', 'peach', 'stewed', 'apple', 'orange', 'pith', 'and', 'pervasive', 'smoke', 'with', 'elements', 'of', 'burnt', 'tobacco', 'an', 'abiding', 'finish', 'of', 'smo

In [432]:
review_vectors = []

for i in range(len(data)):
    clean_review = clean_sentences(data['description'][i])
    vec = make_feature_vec(clean_review,model,\
                           num_features)
    review_vectors.append(vec)
review_vectors

[array([-1.72593128e-02,  5.55468835e-02, -4.61712815e-02,  3.29012796e-02,
        -8.76308233e-02, -6.38189435e-04,  3.75352427e-02,  2.59990748e-02,
         1.92406755e-02,  2.57360539e-03, -1.95201859e-02, -8.18649381e-02,
        -6.23175576e-02,  1.04929775e-01, -7.02063274e-03,  4.93818335e-02,
        -2.51523890e-02, -1.16194654e-02,  6.41817693e-03, -1.92083810e-02,
        -8.05537333e-04, -6.70464113e-02, -1.96274053e-02,  5.54951616e-02,
         7.39398738e-03,  3.06662135e-02,  1.01980470e-01,  7.77846277e-02,
        -1.10191889e-02,  2.55709421e-02, -7.96596110e-02, -7.97692873e-03,
        -9.25770681e-03,  5.65422960e-02,  7.47554703e-03,  5.19490279e-02,
         4.32181545e-02,  2.94183716e-02, -1.51642123e-02, -4.25426662e-02,
        -1.62903406e-02,  2.73362789e-02,  1.12249061e-01,  3.03274859e-02,
        -6.35940442e-03,  3.87172326e-02,  7.64617175e-02, -1.08363340e-02,
         6.60392223e-03,  1.60843749e-02,  4.60131504e-02,  3.56347446e-04,
         3.9

In [433]:
from sklearn.model_selection import train_test_split
from sklearn.naive_bayes import GaussianNB
from sklearn.metrics import accuracy_score

train_predictors, test_predictors, train_target, test_target = \
    train_test_split(review_vectors,data["review.point"],test_size = 0.2)
#min(data["review.point"])
#max(data["review.point"])

# Run Models

In [434]:
gnb = GaussianNB()
gnb.fit(train_predictors,train_target)
gnb_predictions = gnb.predict(test_predictors)
accuracy_score(test_target,gnb_predictions)

0.03111111111111111

In [435]:
#how closs on average ratings are
sum(test_target - gnb_predictions)/len(test_target)

2.3733333333333335

In [436]:
clf = SVC(kernel = 'linear')
clf.fit(train_predictors, train_target)
clf_predictions = clf.predict(test_predictors)
accuracy_score(test_target,clf_predictions)

0.09777777777777778

In [437]:
#how closs on average ratings were
sum(test_target - clf_predictions)/len(test_target)

0.6377777777777778

In [438]:
#accuracy = accuracy_score(train_predictors, train_target)
#whiten = True is important for uncorrelated
#attributes, and is False by default
extractor = PCA(n_components=125, whiten=True)
#When fitting with PCA, you do not use the target column - this is an unsupervised learning algorithm
extractor.fit(train_predictors)

train_predictors_transformed = extractor.transform(train_predictors)
test_predictors_transformed = extractor.transform(test_predictors)

print('this is the variance/importance of each component')
print(extractor.explained_variance_ratio_)
len(train_predictors_transformed)
len(train_target)

this is the variance/importance of each component
[7.35205572e-01 2.12152652e-01 3.17923933e-02 1.70987996e-02
 1.92426451e-03 5.16844872e-04 4.13260024e-04 2.41887101e-04
 1.70348821e-04 1.01313799e-04 7.94004475e-05 5.54362952e-05
 3.50570579e-05 3.38136706e-05 2.73608051e-05 2.08091983e-05
 1.88098829e-05 1.03887947e-05 9.20771070e-06 8.41476804e-06
 7.33597579e-06 5.83213219e-06 5.21703663e-06 4.78662998e-06
 4.33183913e-06 3.23561804e-06 2.80650102e-06 2.67171038e-06
 2.37639350e-06 2.17474533e-06 1.99572332e-06 1.86604117e-06
 1.75919039e-06 1.53743928e-06 1.34639787e-06 1.15469394e-06
 1.08271270e-06 1.05567977e-06 9.94319614e-07 9.16369630e-07
 8.86155897e-07 8.76329482e-07 7.66980550e-07 7.41218271e-07
 6.84160298e-07 6.29998354e-07 6.11418899e-07 5.86486819e-07
 5.59724237e-07 5.46980240e-07 5.09342413e-07 4.81110478e-07
 4.52422654e-07 4.31162224e-07 4.07144718e-07 4.01117683e-07
 3.93498189e-07 3.72452915e-07 3.66053906e-07 3.46989032e-07
 3.28854100e-07 3.15714888e-07 2.98

1797

In [439]:
clfT = SVC(kernel = 'linear')
clfT.fit(train_predictors_transformed, train_target)
clfT_predictions = clfT.predict(test_predictors_transformed)
accuracy_score(test_target,clf_predictions)

0.09777777777777778

In [440]:
#Transformed Gaussian
gnbT = GaussianNB()
gnbT.fit(train_predictors_transformed,train_target)
gnbT_predictions = gnbT.predict(test_predictors_transformed)
accuracy_score(test_target,gnbT_predictions)


0.09333333333333334

# Playing with the model.wc

In [441]:
model.wv.vocab

{'powerful': <gensim.models.keyedvectors.Vocab at 0x1a2bc79940>,
 'and': <gensim.models.keyedvectors.Vocab at 0x1a2bc794a8>,
 'intense': <gensim.models.keyedvectors.Vocab at 0x1a2bc79400>,
 'caramels': <gensim.models.keyedvectors.Vocab at 0x1a2bc792e8>,
 'dried': <gensim.models.keyedvectors.Vocab at 0x1a2bc79390>,
 'elegant': <gensim.models.keyedvectors.Vocab at 0x1a2bc79438>,
 'cigar': <gensim.models.keyedvectors.Vocab at 0x1a2bc79320>,
 'smoke': <gensim.models.keyedvectors.Vocab at 0x1a2bc79908>,
 'from': <gensim.models.keyedvectors.Vocab at 0x1a2bc79eb8>,
 'vanilla': <gensim.models.keyedvectors.Vocab at 0x1a2bc79dd8>,
 'brand': <gensim.models.keyedvectors.Vocab at 0x1a2bc79ef0>,
 'new': <gensim.models.keyedvectors.Vocab at 0x1a2bc79978>,
 'coriander': <gensim.models.keyedvectors.Vocab at 0x1a2bc79e48>,
 'anise': <gensim.models.keyedvectors.Vocab at 0x1a2bc799b0>,
 'make': <gensim.models.keyedvectors.Vocab at 0x1a2bc72550>,
 'for': <gensim.models.keyedvectors.Vocab at 0x1a2bc722b0>,


In [442]:
'elegant' in model.wv.vocab

True

In [443]:
model.wv['elegant']

array([-7.55053619e-03,  7.55888298e-02, -3.96241583e-02,  6.58722187e-04,
       -6.66088089e-02,  2.56753545e-02,  2.18434781e-02,  2.50943154e-02,
        2.96477694e-02,  1.10871531e-02, -3.03511415e-02, -9.51080918e-02,
       -9.62665603e-02,  1.28807977e-01, -5.21432795e-03,  7.29665533e-02,
       -1.48941698e-02, -3.98603082e-02,  2.52058730e-02, -2.71915440e-02,
        1.92910973e-02, -5.51313460e-02, -1.48102148e-02,  6.85845017e-02,
        1.06974766e-02,  2.18245145e-02,  1.13621965e-01,  9.45755318e-02,
       -2.96218358e-02,  5.37923351e-02, -1.14524335e-01, -2.22492218e-02,
       -1.63105167e-02,  5.02468757e-02,  3.42712291e-02,  6.44636676e-02,
        7.73161128e-02,  5.89945242e-02, -6.25073537e-03, -6.88691065e-02,
       -2.25466527e-02,  4.20508869e-02,  1.25916690e-01,  4.29991074e-02,
        2.58853063e-02,  4.83811125e-02,  8.57251883e-02, -3.73527072e-02,
        4.38347831e-02,  2.40625348e-02,  4.55711707e-02,  5.88990515e-03,
       -1.26568768e-02,  

In [444]:
'elegant' in model.wv.vocab

True

In [445]:
model.wv.similarity('good','great')

0.9961979436897678

In [446]:
model.wv.most_similar('elegant')

[('pleasant', 0.9995695352554321),
 ('incredibly', 0.9995139837265015),
 ('effect', 0.9993495345115662),
 ('hard', 0.9992638230323792),
 ('yes', 0.9990744590759277),
 ('freshness', 0.9988991022109985),
 ('vibrant', 0.9988932013511658),
 ('elements', 0.9982988834381104),
 ('starts', 0.9982397556304932),
 ('complexity', 0.998099684715271)]

In [447]:
model.wv.most_similar('dry')

[('lingering', 0.9936081767082214),
 ('spicy', 0.9925360679626465),
 ('lengthy', 0.9809051156044006),
 ('drying', 0.9804087281227112),
 ('medium', 0.9779141545295715),
 ('mouth', 0.9772829413414001),
 ('aniseed', 0.9749946594238281),
 ('slightly', 0.9749400615692139),
 ('plain', 0.9748128652572632),
 ('licorice', 0.9738421440124512)]

In [448]:
model.wv.doesnt_match(['good','elegant','dry','great'])

'dry'

In [449]:
model.wv.most_similar(positive=['dry','spicy'], negative = ['great'])

[('medium', 0.8951462507247925),
 ('finish', 0.8802676796913147),
 ('plain', 0.8730788230895996),
 ('black', 0.8714686036109924),
 ('spices', 0.8700354099273682),
 ('lingering', 0.8673676252365112),
 ('pepper', 0.867182731628418),
 ('licorice', 0.8647930026054382),
 ('dark', 0.8605785965919495),
 ('chocolate', 0.8592739105224609)]

In [450]:
len(train_predictors_transformed)


1797

In [451]:
len(train_target)

1797

In [452]:
first1000 = data["review"][0:1000]

KeyError: 'review'

In [ ]:
len(model.wv.vocab)